# Différentiation Automatique

**(C) Marc BUFFAT, dpt Mécanique, Université Claude Bernard Lyon 1**

![graph](images/graph.gb.png)

In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt

## Problème de minimisation en machine learning

En machine learning, l'objectif est de trouver une loi $U(X,\beta)$ donnant la valeur de $U$ en fonction des données $X$, loi qui dépend des paramètres $\beta$.

Les paramètres $\beta$ sont optimisés de façon à minimiser une fonction coût $J(U)$ à partir d'une base de données où on connait
la valeur de $U$ pour des valeurs de $X$ (apprentissage supervisé).

Pour minimiser $J(U)$ on utilise une méthode de gradient, qui consiste à calculer la nouvelle valeur des paramètres $\beta_{k+1}$:
en se déplaçant dans la direction opposée au gradient de  $J(U)$:

$$ \beta_{k+} = \beta_k - \alpha \nabla_{\beta} J(U(\beta_k)) $$

où

- $\beta_k$ représente les valeurs des paramètres connus du modèle à l'étape k
- $\beta_{k+1}$ les nouvelles valeurs des paramètres
- $\alpha$ est le taux de descente (learning rate)
- $\nabla_{\beta} L$ est le gradient de la fonction coût par rapport aux paramètres

Dans cette méthode de descente, le calcul de ce gradient est la **phase la plus complexe et la plus couteuse,** en particulier lorsque le nombre de paramètres est très important.


### Méthode de calcul du gradient
Pour calculer le gradient de d'une fonction $J(U)$, il existe plusieurs méthodes :


1. **la dérivation symbolique** :
  
  - on calcule la dérivée analytique (à l'aide d'un outil de calcul formel), mais cela suppose une connaissance explicite de $J(U(\beta))$
    
3. **la dérivation numérique** :
   
  - on calcule une approximation numérique par différences finies. C'est en principe le plus simple, mais peut être très coûteux et peu précis

5. **la différentiation automatique** :
   
 - on utilise le code informatique de définition de $J(U)$, qui est sous la forme d'un graphe et la règle dé dérivation composée pour générer un code informatique qui calcule la valeur du gradient

### Exemple simple

Pour présenter ces différentes méthodes, nous allons considérer la minimisation de la fonction $J(x)$ sur l'intervalle $[-3,3]$ suivante:

$$ J(x) = x^3 + x^2 - 6x + 1$$

En traçant la fonction sur $[-3,3]$, on vérifie qu'elle admet bien un minimum local près de 1. 

Nous allons ensuite examiner différentes façon de calculer la valeur de sa dérivée $dJ(x)$

In [ ]:
X = np.linspace(-3,3,101)
J = lambda x: x**3 + x**2 - 6*x + 1
JX = J(X)
plt.plot(X,JX)
plt.title("Fonction J(x)");

## Dérivation symbolique

Sous Python, on va utiliser la bibliothèque sympy et la fonction `Derivative`pour calculer analytiquement le gradient
et la méthode doit() pour faire le calcul immédiatement.

En utilisant la fonction display (au lieu de print), on a un affichage mathématique du résultat.

Pour pouvoir l'utiliser, on va ensuite convertir la fonction symbolique en fonction numpy avec 

In [ ]:
import sympy as sp

x = sp.symbols('x')
expr = x**3 + x**2 - 6*x + 1
display(expr)
DJ = sp.Derivative(expr,x).doit()
display(DJ)

In [ ]:
dJ = sp.lambdify(x,DJ,"numpy")
plt.plot(X,dJ(X))
plt.hlines(0,-3,3)

### Minimisation de J

en utilisant la méthode de descente par gradient (dans ce cas méthode de Newton), on calcule la suite itérative $x_k$ 
$$x_{k+1} = x_k - \alpha*\nabla J(x_k) $$
En partant d'une valeur initiale $x=3$ et en fixant un pas de descente $\alpha=0.1$, on obtiens la position du minimum
avec une précision machine de $10^{-16}$

In [ ]:
x = 3
alpha = 0.1
N = 20
for i in range(N):
    x = x - alpha*dJ(x)
    print(x,J(x),dJ(x))
print("Position du minimum x=",x)

## Dérivation numérique

Au lieu de calculer la dérivée exacte, qui nécessite  la connaissance de l'expression analytique de J, on peut utiliser une dérivation numérique, en utilisant un d'enveloppement de Taylor à l'ordre 1:

$$ J(x+dx) = J(x) + \frac{dJ(x)}{dx} dx + \theta(dx^2)$$

pour obtenir une valeur numérique du gradient en fonction de valeur numérique de J en se fixant un petit accroissement dx de x

$$ dJ = \frac{J(x+dx)-J(x)}{dx} $$

In [ ]:
def dJn(x):
    dx = 0.001
    return (J(x+dx)-J(x))/dx
# tracer
fig = plt.figure(figsize=(10,10))
plt.subplot(2,1,1)
plt.plot(X,dJn(X),label="symbolique")
plt.plot(X,dJ(X),label="numerique")
plt.legend()
plt.title("Gradient de J")
plt.subplot(2,1,2)
plt.title(" Erreur")
plt.plot(X,dJn(X)-dJ(X))
plt.xlabel("x")
plt.tight_layout()

On peut alors utiliser la méthode précédente pour calculer une approximation du minimum de J.

Avec dx=0.01, on constate que la précision du calcul est beaucoup plus faible ($\approx 4.10^{-2}$). Avec
plus petit $dx=0.001$ la précision est ($\approx 4.10^{-3}$). 

La méthode numérique est donc d'ordre 1.

In [ ]:
x = 3
alpha = 0.1
N = 20
for i in range(N):
    x = x - alpha*dJn(x)
print(x,J(x),dJ(x),dJn(x))
print("Position du minimum x=",x)

## Différentiation automatique 

On représente l'expression sous la forme d'un graphe avec l'application de fonctions simples.
Pour la fonction étudiée:

$$ J(x) = x^3 + x^2 - 6x + 1$$

le graphe est donné sur la figure suivante avec les fonctions simples suivantes:

- $f1(x,n) = x^n$
- $f2(x,n) = x*n$
- $g1(x1,x2) = x1 + x2 $
- $g2(x1,x2) = x1 - x2 $

On peut donc écrire:

 $$ J(x) = g1(z1,z2) = g1( g2( g1(f1(x,3),f1(x,2)), f2(x,6)) , 1)$$


In [ ]:
# generation du graph
if False :
    import graphviz

    gr = graphviz.Digraph(filename="graph.gb",format='png')

    names = ["A1","A2","A3","A4","A5","B1","B2","B3","C1","C2","D1","E1"]
    positions =["x","3","2","6","1","f1(x,n)","f1(x,n)","f2(x,n)","g1(x1,x2)","g2(y1,y2)","g1(z1,z2)","J"]
    for name, position in zip(names, positions):
        if name == "A1" :
            gr.node(name, position,color="red",style="filled")
        elif name[0]=="A" :
            gr.node(name, position,color="red")
        elif name == "E1" :
            gr.node(name, position,color="green",style="filled")
        else :
            gr.node(name, position,color="blue",shape = "box")
    # edges
    gr.edge("A1","B1"); gr.edge("A2","B1",label="n"); 
    gr.edge("A1","B2"); gr.edge("A3","B2",label="n")
    gr.edge("A1","B3"); gr.edge("A4","B3",label="n")
    gr.edge("B1","C1",label="x1"); gr.edge("B2","C1",label="x2"); 
    gr.edge("C1","C2",label="y1"); gr.edge("B3","C2",label="y2");
    gr.edge("C2","D1",label="z1"); gr.edge("A5","D1",label="z2")
    gr.edge("D1","E1")
    # display graph
    #display(gr)
    gr.render()
    # second graphe
    gr1 = gr.copy()
    gr1.edge("E1","D1",color="red")
    gr1.edge("D1","C2",color="red");
    gr1.edge("C2","C1",color="red"); gr1.edge("C2","B3",color="red")
    gr1.edge("C1","B1",color="red"); gr1.edge("C1","B2",coor="red"); 
    #display(gr1)
    gr1.render(filename="graph1.gb")

**Graphe directe**

Représentation du DAG: direct acyclic graph dont les noeuds sont des fonctions, les branches entrantes sont les données (tenseurs) et les
branches sortantes les résultats (tenseurs).

![graph](images/graph.gb.png)

 Pour calculer le gradient de J , on utilise la dérivation composée:

 $$ \frac{d F(G(x))}{dx} =  \frac{dF}{dG} \frac{dG}{dx} $$

 ce qui donne

 $$ \nabla J = \frac{\partial g1}{\partial z1} \frac{dz1}{dx} + \frac{\partial g1}{\partial z2} \frac{dz2}{dx}
 \mbox { avec } z1=g2(y1,y2) \mbox{ et } z2 = 1 $$
 
 et ainsi de suite ..

 On constate que, de façon naturel, le calcul du gradient commence par la dérivation de la dernière fonction
 du graph (g1), puis en remontant ensuite dans le graphe. 
 
 C'est l'ordre inverse de l'évaluation de la fonction $J$ et on parle de calcul en mode inverse (reverse mode).

 On parle alors de **reverse mode automatic differentiation**

**Graphe inverse (reverse)**

Parcourt du graph DAC de la racine (root) vers les feuilles (leaves)
(avec les branches en rouge)

![graph1](images/graph1.gb.png)

### Reverse Mode Automatic Differentiation

Un début d'implémentation de ce calcul du gradient en mode **reverse mode** est donné ci-dessous et utilise la notion de `class`de Python avec la possibilité de redéfinir les opérateurs de base.

Le principe est de définir les fonctions simples à partir des opérateurs de base, dont on connaît la dérivée :

- pour $f1(x,n) = x^n $, alors $\frac{f1}{dx} = n x^{n-1}$
- pour $f2(x,x) = n*x $ alors $\frac{f2}{dx} = n $
- pour $g1(x1,x2) = x1 + x2 $ alors $\frac{g1}{dx} = \frac{dx1}{dx} + \frac{dx2}{dx}$
- pour $g2(x1,x2) = x1 - x2 $ alors $\frac{g1}{dx} = \frac{dx1}{dx} - \frac{dx2}{dx}$

On définit pour cela la classe Node avec, pour chaque opérateur / fonction élémentaire, la définition du calcul de la dérivée dans une sous-fonction `backward` utiliser pour le calcul du gradient en **reverse mode**. 

**Remarques** on calcule $df = \frac{df}{dx} \, dx$, on spécifie donc $dx=1$ pour calculer la dérivée

In [ ]:
# classe de base pour décrire l'arbre de calcul de la fonction à minimiser
class Node:
    def __init__(self, value, nom="Node"):
        self.value = value
        self.name = nom+"="+str(value)
        self.grad = 0
        self._backward = lambda: None 
        # this is defined as the forward mode is done based on the computation graph. 
        self._prev = set()

    def __add__(self, other):
        other = other if isinstance(other, Node) else Node(other)
        out = Node(self.value + other.value," + ")
        out._prev = {self, other}
        def _backward():
            self.grad += out.grad
            other.grad += out.grad
        out._backward = _backward
        return out
    
    def __sub__(self, other):
        other = other if isinstance(other, Node) else Node(other)
        out = Node(self.value - other.value," - ")
        out._prev = {self, other}
        def _backward():
            self.grad += out.grad
            other.grad -= out.grad
        out._backward = _backward
        return out

    def __mul__(self, other):
        other = other if isinstance(other, Node) else Node(other)
        out = Node(self.value * other.value," * ")
        out._prev = {self, other}
        def _backward():
            self.grad += other.value * out.grad
            other.grad += self.value * out.grad
        out._backward = _backward
        return out

    def __pow__(self, n):
        out = Node(self.value ** n, " ** ")
        out._prev = {self}

        def _backward():
            self.grad += n * (self.value ** (n-1)) * out.grad 

        out._backward = _backward
        return out

def backward(node):
    topo = []
    visited = set()
    def build_topo(v):
        if v not in visited:
            visited.add(v)
            for child in v._prev:
                build_topo(child)
            topo.append(v)

    build_topo(node)
    # dx = 1
    node.grad = 1
    for node in reversed(topo):
        node._backward()


In [ ]:
# utilisation
x = Node(2.0,"x")
y = x**3 + x**2 - x*6 + 1
backward(y)
# evaluation 
print(f"f(2) = {y.value}, f'(2) = {x.grad}")
print("valeurs exactes ",J(2),dJ(2))

In [ ]:
# evaluation du graphe
x = Node(2.0,"x")
y = x**3 + x**2 - x*6 + 1
topo = []
noms = []
visited = set()
def build_topo(v):
        if v not in visited:
            visited.add(v)
            for child in v._prev:
                build_topo(child)
            topo.append(v)
            noms.append(v.name)
build_topo(y)
# fonction
print("Evaluation f(x) pour x=2 (forward)")
print(noms)
print("F(2)=",noms[-1],y.value)
# gradient
print("Evaluation du gradient")
y.grad = 1
noms = []
grads= []
for node in reversed(topo):
    noms.append(node.name)
    grads.append(node.grad)
    node._backward()
print(noms)
print(grads)
print("Valeur du gradient ",x.grad)

In [ ]:
# tracer de la dérivée
dY = np.zeros(X.size)
for i in range(X.size):
    x = Node(X[i])
    y = x**3 + x**2 - x*6 + 1
    backward(y)
    dY[i] = x.grad
#
plt.subplot(2,1,1)
plt.plot(X,dJn(X),label="symbolique")
plt.plot(X,dY,label="automatique")
plt.legend()
plt.title("Gradient de J")
plt.subplot(2,1,2)
plt.title(" Erreur")
plt.plot(X,dY-dJ(X))
plt.xlabel("x")
plt.tight_layout()

En utilisant la méthode descente par gradient avec les mêmes paramètres que précédemment, on on obtiens la position du minimum
avec une précision machine de $10^{-15}$, c.a.d. la même précision qu'avec le calcul symbolique.

In [ ]:
xa = 3
alpha = 0.1
N = 20
for i in range(N):
    x = Node(xa)
    y = x**3 + x**2 - x*6 + 1
    backward(y) 
    dJa = x.grad
    xa = xa - alpha*dJa
print(xa,y.value,dJa)
print("Position du minimum x=",xa)

### Bibliothèques Python

ce calcul de différentiation automatique est fourni par des bibliothèques Python
 1. Jax  avec en particulier `jax.grad(f)`
 2. PyTorch avec la différentiation automatique torch.autograd, qui est utilisée dans les versions optimisées des réseaux de neurones 
    - https://docs.pytorch.org/tutorials

## Utilisation de pytorch autograd

Pytorch est une bibliothèque Python permettant de manipuler efficacement des tenseurs et disponible en OpenSource.

Parmi les fonctions de Pytorch , `autograd`  est une fonction pour calculer la valeur de la différentielle 
d'une fonction  vectorielle $\mathbf{F}(x)$ de plusieurs composantes, ici 2 composantes  $f(x),g(x)$.

On connaît la valeur $\{F_i=(f_i,g_i)\}$  en N points $\{x_i\}$, et on veut la valeur $\{dF_i\}$ de la différentielle $dF$ en ces N points dans une direction $d\mathbf{l_i}=\{dlf_i, dlg_i \}$ fixée

$$ dF_i = \nabla \mathbf{F}_i . d\mathbf{l}_i = \frac{\partial f_i}{\partial x_i} dlf_i + \frac{\partial g_i}{\partial x_i} dlg_i $$

Le résultat est un vecteur qui peut s'interpréter comme un produit vecteur-Jacobien (vector-Jacobian product) (*attention
ce n'est pas un produit classique matrice vecteur*):

$$
\mathbf{J}^t*d\vec{l} = 
\begin{pmatrix}
\frac{\partial f_1}{\partial x_1} & \frac{\partial g_1}{\partial x_1}\\
\vdots & \vdots\\
\frac{\partial f_n}{\partial x_n} & \frac{\partial g_n}{\partial x_n}\\
\end{pmatrix}
\begin{pmatrix}
dlf_1 & dlg_1\\
\vdots & \vdots\\
dlf_n & dlg_n\\
\end{pmatrix} =
\begin{pmatrix}
dF_1\\
\vdots\\
dF_n\\
\end{pmatrix}
$$

Pour effectuer le calcul numérique il est nécessaire de définir la valeur du vecteur: $\mathbf{dl}_i=\{dlf_i, dlg_i\}$ (noté `grad_output` ou `tensor_output`). En fixant la valeur de $\mathbf{dl}_i$, on choisit la combinaison linéaire des gradients des composantes de $\mathbf{F}$. On note que la dimension de $d\mathbf{l}_i$ est la même que celle de $d\mathbf{F}_i$.

D'un point de vue performance, cela évite de calculer explicitement des matrices (jacobien), mais uniquement des vecteurs.

Si on a une fonction de plusieurs variables, on calcule séparément chacun des gradients par rapport à chacune des variables
en utilisant cette procédure.


### Interface autograd

La classe autograd fournit 2 interfaces: `torch.autograd.grad` et `torch.autograd.backward`

- `torch.autograd.grad(outputs, inputs,grad_outputs)`: Calcule la somme des gradients des tenseurs de sortie (`outputs`) par rapport aux entrées (`inputs`). `grad_inputs` est le vecteur $\mathbf{ds}$ dans le produit vecteur-Jacobien correspondant généralement aux gradients par rapport à chaque élément des tenseurs correspondants. 
- `torch.autograd.backward(tensors,grad_tensors)`: Calcule la somme des gradients des tenseurs (`tensors`) par rapport aux feuilles du graphe. `grad_tensors` est le vecteur $\mathbf{ds}$ dans le produit vecteur-Jacobien correspondant habituellement aux gradients par rapport à chaque élément des tenseurs correspondants.

En termes d’utilisation à haut niveau, on peut considérer `torch.autograd.grad` comme une fonction non mutable.
Comme mentionné dans la documentation, elle n’accumule pas les gradients dans l’attribut grad, mais renvoie directement les dérivées partielles calculées.

En revanche, `torch.autograd.backward` peut modifier les tenseurs en mettant à jour l’attribut grad des nœuds feuilles ; cette fonction ne renvoie aucune valeur.

En d’autres termes, cette dernière est plus adaptée au calcul des gradients pour un grand nombre de paramètres, comme dans les réseaux de neurones.



### Exemple précédent : fonction d'une variable J(x)

Etude de la fonction  $y(x) = x^3 + x^2 - 6x + 1$ sur [-3,3]

On connait la valeur de y : {$y_i$) en N points discrets {$x_i$}. On veut calculer la valeur du gradient en ces points , i.e. 
$$\frac{\partial y_i}{\partial x_i} = (\frac{dy}{dx})(x=x_i)$$

Pour cela `autograd` calcule la différentielle ${dy_i}$ en calculant le gradient $\frac{\partial y_i}{\partial x_i}$ 
à travers la relation:

$$\frac{\partial y_i}{\partial x_i} dx_i =  dy_i$$

Il faut donc choisir  $dx_i=1$ 


In [ ]:
import torch
X = np.linspace(-3,3,101)

Xt =  torch.tensor(X, requires_grad=True)
Yt = Xt**3 + Xt**2 - 6*Xt + 1

In [ ]:
dl = torch.ones_like(Yt)
Yt.backward(gradient=dl)

In [ ]:
dYt = Xt.grad

In [ ]:
# tracer
#plt.plot(Xt.detach().numpy(),dYt)
plt.subplot(2,1,1)
plt.plot(X,dJn(X),label="symbolique")
plt.plot(X,dYt,label="autograd")
plt.legend()
plt.title("Gradient de J")
plt.subplot(2,1,2)
plt.title(" Erreur")
plt.plot(X,dYt-dJ(X))
plt.xlabel("x")
plt.tight_layout()

### Fonction vectorielle

Si on considère maintenant une fonction vectorielle $\mathbf{Y}$ de 2 composantes $\{y1(x),y2(x)\}$ d'une variable x
calculée en N points $x_i$ dont on veut calculer la différentielle par rapport à x

- $x_i$ est un tableau de dimension N
- $Y_i$ est une matrice (N,2)
- $dl_i$ est une matrice (N,2) dont on choisit les valeurs suivant le résultat voulu.

1. pour $dl_i = (1,1)$, on calcule la différentielle $dY_i = \frac{dy1_i}{dx_i} +  \frac{dy2_i}{dx_i}$
2. pour $dl_i = (1,0)$, on calcule la dérivée de $y1$ : $dY_i = \frac{dy1_i}{dx_i} $
3. pour $dl_i = (0,1)$, on calcule la dérivée de $y2$ : $dY_i = \frac{dy2_i}{dx_i} $


In [ ]:
Xt =  torch.tensor(X, requires_grad=True)
Yt  = torch.zeros(X.size,2)
Yt[:,0] = Xt**3 + Xt**2 - 6*Xt + 1
Yt[:,1] = Xt**2 - 2
Yt.shape

In [ ]:
Xt =  torch.tensor(X, requires_grad=True)
Yt  = torch.zeros(X.size,2)
Yt[:,0] = Xt**3 + Xt**2 - 6*Xt + 1
Yt[:,1] = Xt**2 - 2
dl = torch.ones_like(Yt)
Yt.backward(gradient=dl)
dYt=Xt.grad

In [ ]:
Xt =  torch.tensor(X, requires_grad=True)
Yt  = torch.zeros(X.size,2)
Yt[:,0] = Xt**3 + Xt**2 - 6*Xt + 1
Yt[:,1] = Xt**2 - 2
dl = torch.ones_like(Yt)
dl[:,1] = 0 
Yt.backward(gradient=dl)
dY1=Xt.grad

In [ ]:
Xt =  torch.tensor(X, requires_grad=True)
Yt  = torch.zeros(X.size,2)
Yt[:,0] = Xt**3 + Xt**2 - 6*Xt + 1
Yt[:,1] = Xt**2 - 2
dl = torch.ones_like(Yt)
dl[:,0] = 0 
Yt.backward(gradient=dl)
dY2=Xt.grad

In [ ]:
plt.plot(X,dYt,label="dY")
plt.plot(X,dY1,label="dY1")
plt.plot(X,dY2,label="dY2")
plt.plot(X,dY1+dY2,'--',label="dY1+dY2")
plt.xlabel("x")
plt.title("Gradient et différentielle")
plt.legend();

### Fonction de plusieurs variables

On calcule en N points $\{x_i,y_i\}$ la fonction:
$$J(x,y) = xy + sin(x+y)$$
dont on veut calculer les dérivées par rapport à x et à y

Pour cela on calcule la différentielle de J aux N points par rapport à x et par rapport à y. On a donc:

- $\{J_i\}$ vecteur de dimension N
- $\{X_i\}$ $\{Y_i\}$ 2 vecteurs de dimension N
- $\{dl_i\}$ est un vecteur de dimension N  t.q.  $dl_i = 1$
- le résultat est formé par 2 vecteur de dimension $J^x_i$ le gradient par rapport à x et $J^y_i$ le gradient par rapport à y


In [ ]:
# choix des points ou on calcule la fonction
X = -2 + 4*np.random.rand(51)
Y = -2 + 4*np.random.rand(51)
Xt = torch.tensor(X, requires_grad=True)
Yt = torch.tensor(Y, requires_grad=True)
Jt = Xt*Yt + torch.sin(Xt-2*Yt)
# gradient exacte
dJdx = Y + np.cos(X-2*Y)
dJdy = X - 2*np.cos(X-2*Y)

In [ ]:
Jt = Xt*Yt + torch.sin(Xt-2*Yt)
dl = torch.ones_like(Jt)
Jt.backward(gradient=dl)
# résultat
dJtdX = Xt.grad
dJtdY = Yt.grad
print(dJtdX)
print(dJtdY)

In [ ]:
print("Erreur dJdx=",np.mean(dJdx - dJtdX.numpy()))
print("Erreur dJdy=",np.mean(dJdy - dJtdY.numpy()))

### Avec l'interface autograd.grad

In [ ]:
Jt = Xt*Yt + torch.sin(Xt-2*Yt)
dl = torch.ones_like(Jt)
# resultat : 2 vecteurs
torch.autograd.grad(Jt,(Xt,Yt),dl,create_graph=True)

## Références

- https://towardsdatascience.com/automatic-differentiation-autodiff-a-brief-intro-with-examples-3f3d257ffe3b/
- https://medium.com/gaussian-machine/automatic-differentiation-from-scratch-3f95260377f5

## FIN